In [25]:
from rank_bm25 import BM25Plus
import json
from text_untils import *
import pickle

In [26]:
def process_record(record):
    content = record.get('title', '')
    content_id = record.get('_id', '')

    content = clean_text(content)
    content = word_segment(content)
    content = remove_stopword(normalize_text(content))

    return {'id': content_id, 'title': content}

In [27]:
def get_docs(file_path):
    docs = []
    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            try:
                record = json.loads(line)
                doc = process_record(record)
                docs.append(doc)
            except json.JSONDecodeError:
                continue

    return docs
docs = get_docs("./data/cleaned/temp.jsonl")

In [28]:
print(docs)

[{'id': '653a85a21e06875841d12ffb', 'title': 'quy_chuẩn sửa_đổi an_toàn cháy công_trình'}, {'id': '653a85a21e06875841d12ffd', 'title': 'thẩm_quyền điều_động đội phòng cháy chữa_cháy cơ_sở tham_gia hoạt_động chữa_cháy'}, {'id': '653a85a21e06875841d12fff', 'title': 'nhiệm_vụ đội phòng cháy chữa_cháy cơ_sở thế_nào'}, {'id': '653a85a21e06875841d13001', 'title': 'nguyên_tắc phòng cháy chữa_cháy quy_định thế_nào'}, {'id': '653a85a31e06875841d13003', 'title': 'tài_nguyên thiên_nhiên'}, {'id': '653a85a31e06875841d13005', 'title': 'quy_định pháp_luật trách_nhiệm bảo_vệ tài_nguyên thiên_nhiên'}, {'id': '653a85a31e06875841d13007', 'title': 'chính_sách nhà_nước bảo_vệ tài_nguyên thiên_nhiên'}, {'id': '653a85a51e06875841d13009', 'title': 'cống thoát quy_định thế_nào'}, {'id': '653a85a51e06875841d1300b', 'title': 'lập dự_án đầu_tư xây_dựng công_trình cống thoát quy_định thế_nào'}, {'id': '653a85a51e06875841d1300d', 'title': 'trách_nhiệm nghĩa_vụ đơn_vị thoát'}, {'id': '653a85a51e06875841d1300f', 'ti

In [29]:
def save_docs_to_file(docs, output_file):
    with open(output_file, 'w', encoding='utf-8') as file:
        for doc in docs:
            json.dump(doc, file, ensure_ascii=False)
            file.write('\n')

save_docs_to_file(docs, 'output/bm25/docs.jsonl')

In [30]:
with open("./vietnamese.txt", 'r', encoding='utf-8') as file:
    list_stopwords = file.read().splitlines()

In [31]:
texts = [
    [word for word in record.get('title', '').lower().split() if word not in list_stopwords]
    for record in docs
]


In [32]:
print(texts)

[['quy_chuẩn', 'sửa_đổi', 'an_toàn', 'cháy', 'công_trình'], ['thẩm_quyền', 'điều_động', 'đội', 'phòng', 'cháy', 'chữa_cháy', 'cơ_sở', 'tham_gia', 'hoạt_động', 'chữa_cháy'], ['nhiệm_vụ', 'đội', 'phòng', 'cháy', 'chữa_cháy', 'cơ_sở', 'thế_nào'], ['nguyên_tắc', 'phòng', 'cháy', 'chữa_cháy', 'quy_định', 'thế_nào'], ['tài_nguyên', 'thiên_nhiên'], ['quy_định', 'pháp_luật', 'trách_nhiệm', 'bảo_vệ', 'tài_nguyên', 'thiên_nhiên'], ['chính_sách', 'nhà_nước', 'bảo_vệ', 'tài_nguyên', 'thiên_nhiên'], ['cống', 'thoát', 'quy_định', 'thế_nào'], ['lập', 'dự_án', 'đầu_tư', 'xây_dựng', 'công_trình', 'cống', 'thoát', 'quy_định', 'thế_nào'], ['trách_nhiệm', 'nghĩa_vụ', 'đơn_vị', 'thoát'], ['hỗ_trợ', 'thiệt_hại', 'thiên_tai', 'khôi_phục', 'nuôi', 'thủy', 'hải_sản', 'bao_nhiêu'], ['điều_kiện', 'hỗ_trợ', 'thiệt_hại', 'thiên_tai', 'khôi_phục', 'nuôi', 'thủy', 'hải_sản', 'quy_định', 'thế_nào'], ['trình_tự', 'thủ_tục', 'hỗ_trợ', 'thiệt_hại', 'thiên_tai', 'khôi_phục', 'nuôi', 'thủy', 'hải_sản', 'quy', 'thế_nào'], 

In [33]:
bm25plus = BM25Plus(texts)

In [34]:
with open('output/bm25/texts.pkl', 'wb') as f:
    pickle.dump(texts, f)

with open('output/bm25/bm25plus.pkl', 'wb') as f:
    pickle.dump(bm25plus, f)

In [35]:
from skopt import gp_minimize
from skopt.space import Real, Integer
from skopt.utils import use_named_args
from rank_bm25 import BM25Plus

In [36]:
# @use_named_args([(Real(0.01, 2.0, name='k1'), Real(0.1, 1.0, name='b'))])
# def evaluate_bm25plus(k1, b):
#     bm25plus = BM25Plus(texts, k1=k1, b=b)
#
#     score = bm25plus.
#
#     return -score